In [1]:
"""
Created on Tue Feb 12 23:34:44 2019
@author: tobia
"""

import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from oceanoobsbrasil.db import GetData

import os
import glob
from os.path import expanduser
from dotenv import load_dotenv

from pysofar.sofar import SofarApi
from pysofar.spotter import Spotter

In [2]:
%load_ext autoreload
%autoreload 2
from oceanoobsbrasil.others.spotter_data import SpotterData

In [3]:
s = SpotterData()

In [4]:
s.get()

SPOT-0335
No sst data for buoy SPOT-0335 from 2024-01-20 to 2024-01-22
SPOT-0334
No wind data for buoy SPOT-0334 from 2024-01-20 to 2024-01-22
No wave data for buoy SPOT-0334 from 2024-01-20 to 2024-01-22
No sst data for buoy SPOT-0334 from 2024-01-20 to 2024-01-22
SPOT-0746
SPOT-0739
No wind data for buoy SPOT-0739 from 2024-01-20 to 2024-01-22
No wave data for buoy SPOT-0739 from 2024-01-20 to 2024-01-22
No sst data for buoy SPOT-0739 from 2024-01-20 to 2024-01-22
SPOT-0745
No wind data for buoy SPOT-0745 from 2024-01-20 to 2024-01-22
No wave data for buoy SPOT-0745 from 2024-01-20 to 2024-01-22
No sst data for buoy SPOT-0745 from 2024-01-20 to 2024-01-22
SPOT-1272
No sst data for buoy SPOT-1272 from 2024-01-20 to 2024-01-22
SPOT-1293
No sst data for buoy SPOT-1293 from 2024-01-20 to 2024-01-22
SPOT-010065
SPOT-010014
No wind data for buoy SPOT-010014 from 2024-01-20 to 2024-01-22
No wave data for buoy SPOT-010014 from 2024-01-20 to 2024-01-22
No sst data for buoy SPOT-010014 from 20

In [8]:
spotter = s.spotters[10]

In [10]:
spt_data = spotter.grab_data(
    limit=100,
    start_date=s.start_date,
    end_date=s.end_date,
    include_track=True,
    include_wind=True,
    include_surface_temp_data=True,
    include_frequency_data=True,
    include_directional_moments=True,
)

In [11]:
spt_data

{'spotterId': 'SPOT-010069',
 'waves': [{'significantWaveHeight': 4.577,
   'peakPeriod': 11.378,
   'meanPeriod': 8.951,
   'peakDirection': 267.987,
   'peakDirectionalSpread': 30.024,
   'meanDirection': 267.115,
   'meanDirectionalSpread': 38.89,
   'timestamp': '2023-08-08T01:12:25.000Z',
   'latitude': -60.67285,
   'longitude': 151.43072,
   'processing_source': 'embedded'},
  {'significantWaveHeight': 4.857,
   'peakPeriod': 11.378,
   'meanPeriod': 9.314,
   'peakDirection': 270,
   'peakDirectionalSpread': 29.216,
   'meanDirection': 267.254,
   'meanDirectionalSpread': 39.398,
   'timestamp': '2023-08-08T02:12:25.000Z',
   'latitude': -60.66425,
   'longitude': 151.4525,
   'processing_source': 'embedded'},
  {'significantWaveHeight': 4.673,
   'peakPeriod': 12.799,
   'meanPeriod': 9.363,
   'peakDirection': 276.442,
   'peakDirectionalSpread': 23.642,
   'meanDirection': 270.446,
   'meanDirectionalSpread': 35.924,
   'timestamp': '2023-08-08T03:12:25.000Z',
   'latitude':

In [18]:
spec = pd.json_normalize(spt_data, record_path=['frequencyData'], meta=['spotterId'])

In [19]:
spec['buoy_id'] = spotter.id
spec.drop(columns='spotterId', inplace=True)
spec.rename(columns = {'timestamp': 'date_time',
                            }, inplace = True)
if not spec.empty:
    spec.drop(columns='processing_source', inplace=True)
    spec.date_time = pd.to_datetime(spec.date_time)
    spec.date_time = spec.date_time.dt.tz_localize(None)

In [25]:
spec.columns

Index(['frequency', 'df', 'a1', 'b1', 'a2', 'b2', 'varianceDensity',
       'direction', 'directionalSpread', 'date_time', 'latitude', 'longitude',
       'buoy_id'],
      dtype='object')

In [27]:
spec.df.iloc[0]

[0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.00977,
 0.0293,
 0.0293,
 0.0293,
 0.0293,
 0.0293,
 0.0293,
 0.2832]

In [24]:
spec = spec[['frequency', 'direction', 'date_time', 'latitude', 'longitude', 'buoy_id']]

frequency  \
0    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
1    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
2    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
3    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
4    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
..                                                 ...   
446  [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
447  [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
448  [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
449  [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   
450  [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...   

                                                    df  \
0    [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
1    [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
2    [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
3    [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
4    [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
..                                                 ...   
446  [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
447  [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
448  [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
449  [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   
450  [0.00977, 0.00977, 0.00977, 0.00977, 0.00977, ...   

                                                    a1  \
0    [0.172043, 0.139785, 0.178886, 0.692082, 0.851...   
1    [0.057674, 0.029326, 0.108504, 0.565982, 0.830...   
2    [0.129032, 0.178886, 0.320626, 0.770283, 0.907...   
3    [0.164223, 0.117302, 0.389052, 0.766373, 0.878...   
4    [0.044966, 0.134897, 0.345064, 0.828935, 0.903...   
..                                                 ...   
446  [0.549365, 0.538612, 0.369501, 0.616813, 0.715...   
447  [0.410557, 0.414467, 0.305963, 0.589443, 0.720...   
448  [0.502444, 0.494624, 0.296188, 0.611926, 0.740...   
449  [0.57869, 0.576735, 0.244379, 0.631476, 0.7761...   
450  [0.502444, 0.521017, 0.404692, 0.695015, 0.784...   

                                                    b1  \
0    [0.032258, 0.11828, 0.158358, -0.01564, -0.109...   
1    [0.096774, 0.181818, 0.160313, -0.076246, -0.0...   
2    [0.009775, -0.00782, -0.01173, -0.048876, -0.0...   
3    [0.152493, 0.070381, -0.012708, -0.109482, -0....   
4    [0.101662, 0.061584, -0.067449, -0.190616, -0....   
..                                                 ...   
446  [-0.599218, -0.56305, -0.173021, -0.325513, -0...   
447  [-0.553275, -0.494624, -0.185728, -0.410557, -...   
448  [-0.568915, -0.545455, -0.211144, -0.29912, -0...   
449  [-0.498534, -0.468231, -0.176931, -0.301075, -...   
450  [-0.422287, -0.468231, -0.143695, -0.255132, -...   

                                                    a2  \
0    [-0.002933, -0.092864, 0.030303, 0.446725, 0.6...   
1    [-0.044966, -0.034213, 0.049853, 0.356794, 0.6...   
2    [0.226784, 0.206256, 0.335288, 0.556207, 0.761...   
3    [0.232649, 0.189638, 0.313783, 0.527859, 0.730...   
4    [0.131965, 0.11828, 0.242424, 0.641251, 0.7409...   
..                                                 ...   
446  [-0.031281, -0.030303, 0.072336, 0.156403, 0.1...   
447  [-0.139785, -0.107527, -0.075269, 0.053763, 0....   
448  [-0.077224, -0.051808, 0.001955, 0.245357, 0.2...   
449  [0.119257, 0.093842, 0.120235, 0.364614, 0.388...   
450  [0.204301, 0.11437, 0.094819, 0.434995, 0.3870...   

                                                    b2  \
0    [0.2913, 0.202346, 0.066471, 0.008798, -0.1681...   
1    [0.16911, 0.218964, 0.241447, -0.064516, -0.10...   
2    [0.180841, 0.099707, 0.132942, -0.065494, -0.1...   
3    [0.180841, 0.097752, 0.025415, -0.1652, -0.116...   
4    [0.01564, -0.039101, -0.01173, -0.325513, -0.2...   
..                                                 ...   
446  [-0.744868, -0.725318, -0.636364, -0.56696, -0...   
447  [-0.411535, -0.505376, -0.569892, -0.684262, -...   
448  [-0.592375, -0.617791, -0.619746,

In [23]:
pd.DataFrame(spec.frequency.tolist(), index= spec.index)

0        1        2        3        4        5        6        7   \
0    0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
1    0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
2    0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
3    0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
4    0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
..      ...      ...      ...      ...      ...      ...      ...      ...   
446  0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
447  0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
448  0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
449  0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   
450  0.0293  0.03906  0.04883  0.05859  0.06836  0.07813  0.08789  0.09766   

          8        9   ...      29       30       31       32       33  \
0    0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
1    0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
2    0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
3    0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
4    0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
..       ...      ...  ...     ...      ...      ...      ...      ...   
446  0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
447  0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
448  0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
449  0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   
450  0.10742  0.11719  ...  0.3125  0.32227  0.33203  0.35156  0.38086   

          34       35       36       37      38  
0    0.41016  0.43945  0.46875  0.49805  0.6543  
1    0.41016  0.43945  0.46875  0.49805  0.6543  
2    0.41016  0.43945  0.46875  0.49805  0.6543  
3    0.41016  0.43945  0.46875  0.49805  0.6543  
4    0.41016  0.43945  0.46875  0.49805  0.6543  
..       ...      ...      ...      ...     ...  
446  0.41016  0.43945  0.46875  0.49805  0.6543  
447  0.41016  0.43945  0.46875  0.49805  0.6543  
448  0.41016  0.43945  0.46875  0.49805  0.6543  
449  0.41016  0.43945  0.46875  0.49805  0.6543  
450  0.41016  0.43945  0.46875  0.49805  0.6543  

[451 rows x 39 columns]

In [22]:
spec.frequency.

0      [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
1      [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
2      [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
3      [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
4      [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
                             ...                        
446    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
447    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
448    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
449    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
450    [0.0293, 0.03906, 0.04883, 0.05859, 0.06836, 0...
Name: frequency, Length: 451, dtype: object

In [5]:
s.result.head()

name           date_time        lat        lon  wspd  wdir  swvht  \
0  SPOT-010065 2022-07-01 12:31:01 -55.801550  20.779683  10.0   251  3.624   
1  SPOT-010065 2022-07-02 10:21:19 -55.544267  21.169650   6.0   268  4.314   
2  SPOT-010065 2022-07-02 11:21:19 -55.536167  21.195967  10.4   251  4.193   
3  SPOT-010065 2022-07-03 09:15:01 -55.509783  21.737233   6.4   291  3.295   
4  SPOT-010065 2022-07-03 10:15:01 -55.513967  21.756583   9.2   268  3.405   

       tp    wvdir   sst institution data_type   flag  
0  11.378  264.375 -0.44       sofar   drifter  False  
1  11.378  223.872 -0.34       sofar   drifter  False  
2  11.378  231.800 -0.34       sofar   drifter  False  
3   9.309  255.392 -0.40       sofar   drifter  False  
4  10.240  253.806 -0.36       sofar   drifter  False

In [45]:
start_date = (datetime.utcnow() - timedelta(days=3)).strftime('%Y-%m-%d')
end_date = (datetime.utcnow() + timedelta(days=1)).strftime('%Y-%m-%d')

In [48]:
spt_data = s.spotters[15].grab_data(
    limit=100,
    start_date=start_date,
    end_date=end_date,
    include_track=True,
    include_wind=True,
    include_surface_temp_data=True,
    include_frequency_data=False,
    include_directional_moments=True
)

In [54]:
format_date = '%Y-%m-%dT%H:%M:%S.000Z'
wind = pd.json_normalize(spt_data, record_path=['wind'], meta=['spotterId'])
wind.loc[:,'timestamp'] = pd.to_datetime(wind.loc[:,'timestamp'], format = format_date)
wave = pd.json_normalize(spt_data, record_path=['waves'], meta=['spotterId'])
wave.loc[:,'timestamp'] = pd.to_datetime(wave.loc[:,'timestamp'], format=format_date)
sst = pd.json_normalize(spt_data, record_path=['surfaceTemp'], meta=['spotterId'])
sst.loc[:,'timestamp'] = pd.to_datetime(sst.loc[:,'timestamp'], format = format_date)

In [61]:
wave.head()

significantWaveHeight  peakPeriod  ...  longitude    spotterId
0                  2.526      10.240  ...  -36.73440  SPOT-010098
1                  2.424      10.240  ...  -36.71477  SPOT-010098
2                  2.366      10.240  ...  -36.69637  SPOT-010098
3                  2.327       9.309  ...  -36.67853  SPOT-010098
4                  2.372       9.309  ...  -36.66300  SPOT-010098

[5 rows x 11 columns]

In [44]:
s.result

wspd   wdir seasurfaceId  ... meanDirectionalSpread   sst   spotter_id
0     6.0  205.0          2.0  ...                  None  -0.5  SPOT-010065
1     6.4  188.0          2.0  ...                  None  -0.5  SPOT-010065
2     7.6  188.0          2.0  ...                  None  -0.5  SPOT-010065
3     6.0  211.0          2.0  ...                 60.77  -0.5  SPOT-010065
4     6.8  194.0          2.0  ...                  None -0.54  SPOT-010065
..    ...    ...          ...  ...                   ...   ...          ...
979  None   None         None  ...                  None -0.34  SPOT-010126
980  None   None         None  ...                  None -0.66  SPOT-010126
981  None   None         None  ...                  None -0.66  SPOT-010126
982  None   None         None  ...                  None -0.66  SPOT-010126
983  None   None         None  ...                  None -0.66  SPOT-010126

[54062 rows x 15 columns]

In [32]:
s.data[['date_time','latitude','longitude','wspd','wdir','swvht','peakPeriod',
                          'meanDirection', 'sst']]
                          

date_time   latitude  longitude  ... peakPeriod meanDirection   sst
0   2022-06-03 12:13:31  -54.79155  10.258633  ...     12.799       277.879  -0.5
1   2022-06-03 13:13:31 -54.776617   10.26305  ...     12.799       281.835  -0.5
2   2022-06-03 14:13:31  -54.76175  10.266817  ...     12.799        277.61  -0.5
3   2022-06-03 15:13:31   -54.7455   10.27225  ...     12.799       278.916  -0.5
4   2022-06-03 16:13:31 -54.730233  10.276017  ...     11.378       273.241 -0.54
..                  ...        ...        ...  ...        ...           ...   ...
755 2022-06-19 20:42:01       None       None  ...       None          None -0.34
756 2022-07-02 13:53:01       None       None  ...       None          None -0.66
757 2022-07-02 14:13:01       None       None  ...       None          None -0.66
758 2022-07-02 14:53:01       None       None  ...       None          None -0.66
759 2022-07-02 15:13:01       None       None  ...       None          None -0.66

[41356 rows x 9 columns]

In [4]:
bd = GetData()

In [4]:
bd.get(table='stations', institution=['=', 'simcosta'], data_type=['=', 'buoy'])

id name         lat         lon data_type institution url
0  897  RJ3    -22.9831    -43.1745      buoy    simcosta   3
1  898  RS2    -32.1346 -52098.0000      buoy    simcosta   6
2  899  RS5 -32296.0000    -52.0239      buoy    simcosta  10
3  900  RJ4    -22.9715    -43.1522      buoy    simcosta  12
4  901  RS3 -32195.0000    -52.0794      buoy    simcosta  13
5  902  RS4    -32.2454    -52.0954      buoy    simcosta  14
6  903  BA1    -12.9895    -37.4582      buoy    simcosta  15

In [8]:
df = bd.get(table='data_stations', station_id=['in', [902]])

In [9]:
df.shape

(94, 22)

In [7]:
bd.post(table='data_stations', df=df)

DELETE FROM data_stations WHERE true AND station_id in (902) AND date_time >= '2021-09-06 00:21:00'


In [5]:
import time
import datetime
import operator
import urllib.request, json

import numpy as np
from oceanoobsbrasil.buoys.simcosta import Simcosta
from oceanoobsbrasil.tides.simcosta import SimcostaTide

In [6]:
s = SimcostaTide()

In [7]:
s.get()

Nao ha dados para essa boia
Nao ha dados para essa boia
Nao ha dados para essa boia


In [8]:
s = Simcosta()

In [9]:
s.get()

210
Nao ha dados para essa boia
504
Nao ha dados para essa boia
15
ok
3
ok
12
ok
14
Nao ha dados para essa boia
13
Nao ha dados para essa boia
510
ok
6
Nao ha dados para essa boia


In [5]:
from oceanoobsbrasil.buoys.pnboia import Pnboia

In [7]:
p = Pnboia()
p.get()

alcatrazes
Dados inseridos
bacia_de_santos
'date_time'
abrolhos
Dados inseridos
almirantado
'date_time'
noronha
Dados inseridos
mexilhão
'date_time'
pinguim
'date_time'
keller
'date_time'
bacia_de_campos
'date_time'
imbituba
Dados inseridos


In [43]:
s.result.drop(columns=columns, inplace=True)

In [44]:
s.result.columns = ['pres', 'atmp', 'rh', 'dewpt', 'wspd', 'wdir', 'gust', 'swvht', 'mxwvht', 'tp', 'sst', 'wvspread', 'wvdir', 'date_time']

In [45]:
s.result = s.result.replace(to_replace =['None', 'NULL', ' ', ''],
                                        value =np.nan)

In [46]:
s.result['station_id'] = 898

In [ ]:
s.